In [110]:
import pandas as pd
import numpy as np
import json
import folium
import os
from geopy.geocoders import Nominatim

# Foursquare

In [371]:
# Export the foursquare dataset
foursquare = pd.read_csv('../data/foursquare/all.csv')

# Drop duplicates
foursquare.drop_duplicates(subset = 'id', inplace=True, ignore_index=True)

# Process the data to group categories
def process_categories(category_name):
    
    # Restaurant and Bar
    restaurant = ['restaurant', 'bar', 'café', 'cafe', 'coffee', 'pizza', 'sandwich', 'breakfast spot', 'ice cream',
                  'frozen yogurt', 'speakeasy', 'nightlife', 'diner', 'lounge', 'joint', 'snack', 'bistro', 'food truck',
                  'brewery', 'strip club', 'pub', 'nightclub', 'food court', 'steakhouse', 'tea room', 'taco', 'castle',
                  'creperie', 'buffet', 'food service', 'bath house', 'poke place', 'soup place', 'club house',
                  'fish & chips', 'burrito', 'poutine', 'noodle', 'brasserie', 'well', 'salad place', 'beer garden']
    for r in restaurant:
        if r in str(category_name).lower() and str(category_name) not in ['Salon / Barbershop', 'Piano Bar', 'Public Art']:
            return 'Restaurant/Bar'
    
    # Kids care (school, day care, playground, ...)
    kids = ['care', 'playground']
    for k in kids:
        if k in str(category_name).lower():
            return 'KidCare'
    
    # Entertainment
    entertainment = ['museum', 'theater', 'entertainment', 'event space', 'art gallery', 'performing', 'public art',
                     'art studio', 'library', 'design', 'music venue', 'comedy', 'photography', 'sculpture',
                     'convention center', 'arcade', 'bowling', 'recreation', 'rock', 'jazz', 'concert', 'auditorium',
                     'water', 'monument', 'lighthouse', 'exhibit', 'planetarium', 'recording studio', 'memorial site',
                     'piano', 'circus', 'zoo', 'spa', 'massage', 'casino', 'play area']
    for e in entertainment:
        if e in str(category_name).lower():
            return 'Entertainment/Culture'
    
    # Services
    services = ['store', 'shop', 'service', 'pharmacy', 'bank', 'bakery', 'gas station', 'government', 'bodega',
                'salon', 'post', 'rental car', 'veterinarian', 'boutique', 'car wash', 'tattoo', 'butcher', 'real estate',
                'auto', 'storage', 'market', 'parking', 'atm', 'lawyer', 'funeral', 'food', 'cleaner', 'embassy',
                'driving', 'agency', 'courthouse', 'repair', 'winery', 'grocery', 'animal', 'notary', 'food stand',
                'credit union', 'locksmith', 'laundromat', 'general travel']
    for s in services:
        if s in str(category_name).lower():
            return 'Services'
    
    # Sports
    sports = ['pool', 'gym', 'sports', 'field', 'studio', 'court', 'rink', 'golf', 'arena', 'track', 'stadium',
              'skate', 'range', 'dojo', 'curling']
    for s in sports:
        if s in str(category_name).lower():
            return 'Sports'
    
    # Outdoor
    outdoor = ['park', 'outdoor', 'scenic lookout', 'site', 'garden', 'marina', 'boat', 'plaza', 'trail', 'mountain', 'surf',
               'campground', 'lake', 'beach', 'rest area', 'vineyard', 'forest', 'nature', 'cave', 'fishing', 'rafting']
    for o in outdoor:
        if o in str(category_name).lower():
            return 'Outdoor'
    
    # Medical
    medical = ['dentist', 'doctor', 'medical', 'hospital', 'assisted living', 'chiropractor', 'mental', 'healer',
               'emergency', 'therapist', 'laboratory', 'acupuncturist', 'clinic']
    for m in medical:
        if m in str(category_name).lower():
            return 'Medical'
    
    # Religious
    religious = ['church', 'synagogue', 'temple', 'spiritual', 'mosque', 'shrine']
    for r in religious:
        if r in str(category_name).lower():
            return 'Religious'
    
    # All other
    if pd.isna(category_name):
        category = 'Other'

    return 'Other'
    

foursquare['category'] = foursquare['category_name'].apply(process_categories)
foursquare['category'].value_counts()

Other                    3405
Services                 3400
Restaurant/Bar           1958
Entertainment/Culture     717
Medical                   459
Sports                    451
Outdoor                   416
Religious                 172
KidCare                   124
Name: category, dtype: int64

# STM

Let's get the fsa for each metro stations and save it in a CSV file. There's no need to do it each time as long as the CSV file is available.

In [145]:
# Get the data from the geojson file for each metro station
with open('../data/metro/metro_stations.geojson') as f:
    data = json.load(f)
metro = []
for feature in data['features']:
    if feature['geometry'] is not None:
        station = {}
        station['Name'] = feature['properties']['stop_name']
        station['Latitude'] = feature['geometry']['coordinates'][1]
        station['Longitude'] = feature['geometry']['coordinates'][0]
        metro.append(station)

# Get the addresses from the coordinates to have the fsa
geolocator = Nominatim(user_agent='mtl')
for m in metro:
    location = geolocator.reverse(str(m['Latitude']) + ', ' + str(m['Longitude']))
    m['fsa'] = location.address.split(',')[-2][1:4]

# Save the data into a csv file to have it for the next times
pd.DataFrame(metro).to_csv('../data/metro/metro_stations.csv')

In [370]:
pd.DataFrame(metro).head()

Name   Latitude  Longitude  fsa
0     Station Angrignon  45.446466 -73.603118  H8N
1          Station Monk  45.451158 -73.593242  H4E
2     Station Jolicoeur  45.457010 -73.581691  H4E
3        Station Verdun  45.459441 -73.572021  H4G
4  Station De l'Ã‰glise  45.461894 -73.567074  H4G

# Schools

In [364]:
# Get the data from the CSV files
college = pd.read_csv('../data/schools/ES_Collegial.csv', sep=';')
univ = pd.read_csv('../data/schools/ES_Universitaire.csv', sep=';')
pps_gouv = pd.read_csv('../data/schools/PPS_Gouvernemental.csv', sep=';')
pps_prive = pd.read_csv('../data/schools/PPS_Prive_Installation.csv', sep=';')
pps_public = pd.read_csv('../data/schools/PPS_Public_Ecole.csv', sep=';')
pps_public.rename(columns={'CD_POSTL_GDUNO_ORGNS': 'CD_POSTL_GDUNO'}, inplace=True)

# Keep only the schools in the Montreal island
def mtl_fsa(postal_code):
    if postal_code[0:2] in ['H1', 'H2', 'H3', 'H4', 'H5', 'H8', 'H9']:
        return True
    else:
        return False
college = college[college['CD_POSTL_GDUNO'].apply(mtl_fsa)].reset_index(drop=True)
univ = univ[univ['CD_POSTL_GDUNO'].apply(mtl_fsa)].reset_index(drop=True)
pps_gouv = pps_gouv[pps_gouv['CD_POSTL_GDUNO'].apply(mtl_fsa)].reset_index(drop=True)
pps_prive = pps_prive[pps_prive['CD_POSTL_GDUNO'].apply(mtl_fsa)].reset_index(drop=True)
pps_public = pps_public[pps_public['CD_POSTL_GDUNO'].apply(mtl_fsa)].reset_index(drop=True)

# Duplicate rows with multiple school levels and separate the name to have one row for one school level
def school_level(school):
    for i in school.index:
        s = school.loc[i, 'ORDRE_ENS'].split('-')
        if len(s) > 1:
            for j in range(1, len(s)):
                m = max(school.index)+1
                school.loc[m] = school.loc[i]
                school.loc[m, 'ORDRE_ENS'] = s[j]
                if school.loc[m, 'ORDRE_ENS'][0] == ' ':
                    school.loc[m, 'ORDRE_ENS'] = school.loc[m, 'ORDRE_ENS'][1:]
                if school.loc[m, 'ORDRE_ENS'][-1] == ' ':
                    school.loc[m, 'ORDRE_ENS'] = school.loc[m, 'ORDRE_ENS'][:-1]
            school.loc[i, 'ORDRE_ENS'] = s[0]
            school.loc[i, 'ORDRE_ENS'] = school.loc[i, 'ORDRE_ENS'][:-1]
    school.sort_values(by=['OBJECTID'], inplace=True)
    school.reset_index(drop=True, inplace=True)
    return school
pps_prive = school_level(pps_prive)
pps_public = school_level(pps_public)

# Create a dataframe containing all the schools with the FSA and the school level
schools = pd.concat([college[['OBJECTID', 'CD_POSTL_GDUNO', 'ORDRE_ENS']],
                     univ[['OBJECTID', 'CD_POSTL_GDUNO', 'ORDRE_ENS']],
                     pps_gouv[['OBJECTID', 'CD_POSTL_GDUNO', 'ORDRE_ENS']],
                     pps_prive[['OBJECTID', 'CD_POSTL_GDUNO', 'ORDRE_ENS']],
                     pps_public[['OBJECTID', 'CD_POSTL_GDUNO', 'ORDRE_ENS']]])
schools['CD_POSTL_GDUNO'] = schools['CD_POSTL_GDUNO'].apply(lambda x: x[0:3])
schools.rename(columns={'OBJECTID': 'SchoolId', 'CD_POSTL_GDUNO': 'fsa', 'ORDRE_ENS': 'Level'}, inplace=True)
schools.sort_values(by=['fsa'], inplace=True)
schools.reset_index(drop=True, inplace=True)
schools = schools.groupby(['fsa', 'Level']).agg(NbSchool=('SchoolId','count')).reset_index()

In [369]:
schools.head()

fsa                      Level  NbSchool
0  H1A                   Primaire         9
1  H1A                Préscolaire         9
2  H1A                 Secondaire         5
3  H1B  Formation professionnelle         2
4  H1B                   Primaire         7

# FSA

Let's see all the available and not available walkscores, transitscores and bikescores on the map.

In [99]:
latitude = 45.505331312
longitude = -73.55249779
mtl_geo_json = "../data/mtl_fsa_map.geojson"

ws = pd.read_csv('../data/walkscore/walkscore.csv')
ws.drop(ws.columns[ws.apply(lambda col: 'Unnamed' in str(col))], axis=1, inplace=True)

score = 'Walkscore' # 'Walkscore' or 'Transitscore' or 'Bikescore'

nan_ws_map = folium.Map(location=[latitude, longitude], zoom_start=10)
for lat, lng, score in zip(ws['latitude'], ws['longitude'], ws[score]):
    label = folium.Popup(str(score), parse_html=True)
    if np.isnan(score):
        folium.CircleMarker(
            [lat, lng],
            radius=1,
            popup=label,
            color='red',
            parse_html=False).add_to(nan_ws_map)
    else:
        folium.CircleMarker(
            [lat, lng],
            radius=1,
            popup=label,
            color='blue',
            parse_html=False).add_to(nan_ws_map)
    
nan_ws_map

The available walkscores and bikescores can be processed but the transitscores are not relevant because they are too concentrated on a single geographic area.

In [71]:
ws_processed = ws.groupby('fsa', as_index=False).mean()
ws_processed.drop(columns='Transitscore', inplace=True)
ws_processed

fsa   latitude  longitude  Walkscore  Bikescore
0   H1A  45.670741 -73.505878  20.512987  54.922078
1   H1B  45.635377 -73.523538  17.962406  47.503759
2   H1C  45.669124 -73.534936   4.640351  47.166667
3   H1E  45.638857 -73.583131  32.710526  54.692982
4   H1G  45.612047 -73.620212  49.362500  60.087500
..  ...        ...        ...        ...        ...
92  H9P  45.466971 -73.753479  14.785714  43.681818
93  H9R  45.460418 -73.812499  32.463576  55.549669
94  H9S  45.440306 -73.781397  37.726316  68.200000
95  H9W  45.430156 -73.869548  19.686957  49.495652
96  H9X  45.426168 -73.934695  10.895735  49.924171

[97 rows x 5 columns]

Let's see the choropleth map of Montreal for the walkscores and bikescores:

In [100]:
score = 'Walkscore' # 'Walkscore' or 'Bikescore'
bins = {'Walkscore': [0, 25, 50, 70, 90, 100],
        'Bikescore': [0, 50, 70, 90, 100]}

ws_map = folium.Map(location=[latitude, longitude], zoom_start=10)
label = folium.Popup(lgd[score], parse_html=True)
folium.Choropleth(
    geo_data=mtl_geo_json,
    data=ws_processed,
    columns=['fsa', 'Walkscore'],
    key_on='feature.properties.CFSAUID',
    fill_color='BuPu',
    fill_opacity=0.8, 
    line_opacity=0.2,
    bins=bins[score],
    legend_name=score,
    popup=label
).add_to(ws_map)

ws_map

Walkscore:
- 0-25: Car-dependent *(almost all errands require a car)*
- 25-50: Car-dependent *(most errands require a car)*
- 50-70: Somewhat walkable *(some errands can be accomplished on foot)*
- 70-90: Very walkable *(most errands can be accomplished on foot)*
- 90-100: Walker's paradize *(daily errands do not require a car)*

Bikescore:
- 0-50: Somewhat bikeable *(minimal bike infrastructure)*
- 50-70: Bikeable *(some bike infrastructure)*
- 70-90: Very bikeable *(biking is convenient for most trips)*
- 90-100: Biker's paradize *(daily errands can be accomplished on a bike)*

# Cleaning FSA

In [185]:
def get_fsa_points(fsa):
    # Get the coordinates for the generated points
    folder_path = '../data/walkscore/FSApoints'
    read_data = []
    for (dirpath, dirnames, filenames) in os.walk(folder_path):
        if fsa is not None:
            filenames = ['{}.geojson'.format(fsa)]
        for file_name in filenames:
            with open(os.path.join(dirpath, file_name)) as f:
                read_data.append(json.load(f))
    data = []
    for f in read_data:
        fsa = f['name']
        for feature in f['features']:
            if feature['geometry'] is not None:
                point = {}
                point['fsa'] = fsa
                point['latitude'] = feature['geometry']['coordinates'][1]
                point['longitude'] = feature['geometry']['coordinates'][0]
                data.append(point)

    return data

In [186]:
points = pd.DataFrame(get_fsa_points(None))
points

fsa   latitude  longitude
0     H1A  45.672993 -73.501745
1     H1A  45.699057 -73.507709
2     H1A  45.646386 -73.534093
3     H1A  45.650656 -73.539455
4     H1A  45.670163 -73.502179
...   ...        ...        ...
5041  H9X  45.429366 -73.969428
5042  H9X  45.414927 -73.959636
5043  H9X  45.429497 -73.933132
5044  H9X  45.432233 -73.942556
5045  H9X  45.432537 -73.923004

[5046 rows x 3 columns]

In [188]:
ws1 = pd.read_csv('../data/walkscore/walkscore_in_water.csv')
ws1.drop(ws1.columns[ws1.apply(lambda col: 'Unnamed' in str(col))], axis=1, inplace=True)
ws1

fsa   latitude  longitude  Walkscore WalkscoreDescription  Transitscore  \
0     H1A  45.667314 -73.487601        9.0        Car-Dependent           NaN   
1     H1A  45.672993 -73.501745       29.0        Car-Dependent          54.0   
2     H1A  45.692476 -73.480646       19.0        Car-Dependent           NaN   
3     H1A  45.699057 -73.507709        1.0        Car-Dependent          37.0   
4     H1A  45.700183 -73.493876        8.0        Car-Dependent           NaN   
...   ...        ...        ...        ...                  ...           ...   
6255  H9X  45.429366 -73.969428        0.0        Car-Dependent           NaN   
6256  H9X  45.414927 -73.959636        8.0        Car-Dependent           NaN   
6257  H9X  45.429497 -73.933132        6.0        Car-Dependent           NaN   
6258  H9X  45.432233 -73.942556        5.0        Car-Dependent           NaN   
6259  H9X  45.432537 -73.923004       11.0        Car-Dependent           NaN   

     TransitDescription  Bikescore    BikeDescription  
0                   NaN       44.0  Somewhat Bikeable  
1          Good Transit       62.0           Bikeable  
2                   NaN       44.0  Somewhat Bikeable  
3          Some Transit       52.0           Bikeable  
4                   NaN       36.0  Somewhat Bikeable  
...                 ...        ...                ...  
6255                NaN       51.0           Bikeable  
6256                NaN       51.0           Bikeable  
6257                NaN       51.0           Bikeable  
6258                NaN       34.0  Somewhat Bikeable  
6259                NaN       64.0           Bikeable  

[6260 rows x 9 columns]

In [189]:
# points[['latitude']].apply(lambda x: round(x, 8))
for i in points.index.values:
    points.loc[i, 'latitude'] = round(points.loc[i, 'latitude'], 8)
    points.loc[i, 'longitude'] = round(points.loc[i, 'longitude'], 8)
for i in ws1.index.values:
    ws1.loc[i, 'latitude'] = round(ws1.loc[i, 'latitude'], 8)
    ws1.loc[i, 'longitude'] = round(ws1.loc[i, 'longitude'], 8)

In [190]:
test = pd.concat([points, ws1])
test
df = test[test.duplicated(subset=['fsa', 'latitude', 'longitude'])]
df.reset_index(drop=True, inplace=True)
df
df.to_csv('../data/walkscore/walkscore.csv')

fsa   latitude  longitude  Walkscore WalkscoreDescription  Transitscore  \
0     H1A  45.672993 -73.501745       29.0        Car-Dependent          54.0   
1     H1A  45.699057 -73.507709        1.0        Car-Dependent          37.0   
2     H1A  45.646386 -73.534093        0.0        Car-Dependent          37.0   
3     H1A  45.650656 -73.539455       15.0        Car-Dependent          43.0   
4     H1A  45.670163 -73.502179       37.0        Car-Dependent          54.0   
...   ...        ...        ...        ...                  ...           ...   
5041  H9X  45.429366 -73.969428        0.0        Car-Dependent           NaN   
5042  H9X  45.414927 -73.959636        8.0        Car-Dependent           NaN   
5043  H9X  45.429497 -73.933132        6.0        Car-Dependent           NaN   
5044  H9X  45.432233 -73.942556        5.0        Car-Dependent           NaN   
5045  H9X  45.432537 -73.923004       11.0        Car-Dependent           NaN   

     TransitDescription  Bikescore    BikeDescription  
0          Good Transit       62.0           Bikeable  
1          Some Transit       52.0           Bikeable  
2          Some Transit       34.0  Somewhat Bikeable  
3          Some Transit       35.0  Somewhat Bikeable  
4          Good Transit       67.0           Bikeable  
...                 ...        ...                ...  
5041                NaN       51.0           Bikeable  
5042                NaN       51.0           Bikeable  
5043                NaN       51.0           Bikeable  
5044                NaN       34.0  Somewhat Bikeable  
5045                NaN       64.0           Bikeable  

[5046 rows x 9 columns]